## Libraries

In [12]:
import pandas as pd
import psycopg2
import folium
from IPython.display import display

# Extract

In [24]:
# Load the CSV file
def extract_data(file_path):
    try:
        data = pd.read_csv(file_path)
        return data
    except Exception as e:
        print(f"Error occurred while reading the file: {e}")
        return None

In [25]:
# Path to CSV
file_path = 'Address list - Sheet1.csv'  
raw_data = extract_data(file_path)

# Transform

### Drop Null

In [ ]:
data = data.dropna(subset=['address', 'lat', 'lng'])

### Split addresses and drop null

In [21]:
def transform_data(data):
   
    #Function to split the address into components
    def split_address(address):
        try:
            parts = address.split(',')
            house_no = parts[0].split()[0]
            city = parts[1].strip()
            state_zip = parts[2].strip().split(' ')
            state_code = state_zip[0]
            zip_code = state_zip[1]
            return house_no, city, state_code, zip_code
        except Exception as e:
            print(f"Error splitting address: {e}")
            return None, None, None, None

    #Apply the address splitting function to the dataframe
    data.loc[:,['house_no', 'city', 'state_code', 'zip_code']] = data.apply(
        lambda row: pd.Series(split_address(row['address'])), axis=1
    )

    #Sort by state_code and city
    data = data.sort_values(by=['state_code', 'city'])

    return data

#Transform the extracted data
cleaned_data = transform_data(raw_data)


In [23]:
cleaned_data.to_csv('data.csv', index=False)

# Load

### Connect to the PostgreSQL database

In [5]:
def connect_to_db():
    try:
        #my database props
        conn = psycopg2.connect(
            host="localhost",
            database="postgres",
            user="postgres",
            password="admin"
        )
        return conn
    except Exception as e:
        print(f"Error connecting to the database: {e}")
        return None

### Create PostgreSQL table 'Addresses'

In [29]:
# create table as given in the instructions
def create_table(conn):
    with conn.cursor() as cursor:
        cursor.execute('''
            CREATE TABLE IF NOT EXISTS addresses (
                id SERIAL PRIMARY KEY,
                house_no VARCHAR(10),
                city VARCHAR(50),
                state_code VARCHAR(2),
                zip_code VARCHAR(10),
                lat DOUBLE PRECISION,
                lng DOUBLE PRECISION
            );
        ''')
        conn.commit()

### Insert data into the table

In [30]:
def insert_data(conn, data):
    with conn.cursor() as cursor:
        for _, row in data.iterrows():
            cursor.execute('''
                INSERT INTO addresses (house_no, city, state_code, zip_code, lat, lng)
                VALUES (%s, %s, %s, %s, %s, %s)
            ''', (row['house_no'], row['city'], row['state_code'], row['zip_code'], row['lat'], row['lng']))
        conn.commit()

### Function call

In [44]:
conn = connect_to_db()

if conn:
    create_table(conn)  
    insert_data(conn, cleaned_data)  
    conn.close() 

# Bonus

## SQL query 

In [6]:
# Function to execute the SQL query and fetch results
def get_state_address_counts():
    conn = connect_to_db()
    cursor = conn.cursor()

    # SQL query to count addresses for each state
    query = '''
        SELECT state_code, COUNT(*) AS address_count
        FROM addresses
        GROUP BY state_code
        ORDER BY state_code;
    '''
    
    # Execute the query
    cursor.execute(query)
    
    # Fetch the result
    results = cursor.fetchall()
    
    # Close the connection
    cursor.close()
    conn.close()

    return results

In [9]:
# Fetch the results
state_address_counts = get_state_address_counts()

# Convert the results into a pandas DataFrame
df = pd.DataFrame(state_address_counts, columns=['State Code', 'Address Count'])

# Save the DataFrame to a CSV file
csv_file_path = 'state_address_counts(bonus query).csv'
df.to_csv(csv_file_path, index=False)

## Display the addresses

In [45]:
# Fetch address data (latitude and longitude) from the PostgreSQL database
def fetch_address_data():
    conn = connect_to_db()
    cursor = conn.cursor()
    cursor.execute('SELECT lat, lng, house_no, city, state_code, zip_code FROM addresses')
    rows = cursor.fetchall()  # Fetch all rows
    cursor.close()
    conn.close()
    return rows

In [46]:
# Generate the Folium map with the address data and display it in the notebook
def display_map(address_data):
    # Initialize a Folium map centered at a specific location (adjust if needed)
    folium_map = folium.Map(location=[40.7128, -74.0060], zoom_start=5)

    # Loop through the address data and add each location to the map
    for address in address_data:
        lat, lng, house_no, city, state_code, zip_code = address
        # Create a popup description for each marker
        popup_text = f'{house_no}, {city}, {state_code} {zip_code}'
        folium.Marker(location=[lat, lng], popup=popup_text).add_to(folium_map)

    # Display the map inline in the notebook
    display(folium_map)

In [47]:
# Fetch the data
address_data = fetch_address_data()

# Display the map
display_map(address_data)